In [1]:
import optuna
import numpy as np
import optuna.visualization as vis
import os

/home/samar/anaconda3/envs/grad/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
def generate_tracks(path,d):
    track_high_thresh = d['track_high_thresh']
    track_low_thresh = d['track_low_thresh']
    new_track_thresh = d['new_track_thresh']
    track_buffer = d['track_buffer']
    match_thresh = d['match_thresh']
    nms_thres = d['nms_thres']
    proximity_thresh = d['proximity_thresh']
    appearance_thresh = d['appearance_thresh']
    for video in sorted(os.listdir(path)):
        videopath = os.path.join(path,video)
        os.system(f"python demo.py --path {videopath} --track_high_thresh {track_high_thresh} --track_low_thresh {track_low_thresh} --new_track_thresh {new_track_thresh} --track_buffer {track_buffer} --match_thresh {match_thresh} --nms_thres {nms_thres} --proximity_thresh {proximity_thresh} --appearance_thresh {appearance_thresh}")

In [3]:
path = "/media/samar/HDD1T/Deep-EIoU/Deep-EIoU/tools/test_videos"
tracks_path = "/media/samar/HDD1T/Deep-EIoU/Deep-EIoU/tools/YOLOX_outputs/yolox_x_ch_sportsmot/track_vis"
def objective(trial):
    track_high_thresh = trial.suggest_float("track_high_thresh",low=0.3,high=0.95,step=0.05)
    track_low_thresh = trial.suggest_float("track_low_thresh",low=0.05,high=0.3,step=0.05)
    new_track_thresh = trial.suggest_float("new_track_thresh",low=0.05,high=0.95,step=0.05)
    track_buffer = trial.suggest_int("track_buffer",low=1,high=750,step=1)
    match_thresh = trial.suggest_float("match_thresh",low=0.05,high=0.95,step=0.05)
    nms_thres = trial.suggest_float("nms_thres",low=0.05,high=0.95,step=0.05)
    proximity_thresh = trial.suggest_float("proximity_thresh",low=0.05,high=0.95,step=0.05)
    appearance_thresh = trial.suggest_float("appearance_thresh",low=0.05,high=0.95,step=0.05)
    d = {

        'track_high_thresh':track_high_thresh,
        'track_low_thresh':track_low_thresh,
        'new_track_thresh':new_track_thresh,
        'track_buffer':track_buffer,
        'match_thresh':match_thresh,
        'nms_thres':nms_thres,
        'proximity_thresh':proximity_thresh,
        'appearance_thresh':appearance_thresh
    }

    generate_tracks(path,d)
    #os.system(f"cd {tracks_path}")
    os.chdir(tracks_path)
    os.system("zip tracker *.txt")
    os.system("mv tracker.zip  /media/samar/HDD1T/Deep-EIoU/Deep-EIoU/tools/SN_TRACKING_HOME/tools")
    os.chdir("/media/samar/HDD1T/Deep-EIoU/Deep-EIoU/tools/SN_TRACKING_HOME/tools")
    #os.system("cd /media/samar/HDD1T/Deep-EIoU/Deep-EIoU/tools/SN_TRACKING_HOME/tools")
    os.system("python evaluate_soccernet_v3_tracking.py --TRACKERS_FOLDER_ZIP tracker.zip --GT_FOLDER_ZIP gt.zip --BENCHMARK SNMOT --DO_PREPROC False --SEQMAP_FILE SNMOT-test.txt --TRACKERS_TO_EVAL test --SPLIT_TO_EVAL test --OUTPUT_SUB_FOLDER eval_results")
    os.system("rm tracker.zip")
    os.system("rm -r temp")
    score = float(np.load("HOTA.npy"))
    os.system("rm HOTA.npy")
    os.chdir("/media/samar/HDD1T/Deep-EIoU/Deep-EIoU/tools")
    #os.system("cd /media/samar/HDD1T/Deep-EIoU/Deep-EIoU/tools")
    os.system("rm -r YOLOX_outputs")
    #os.system("cd /media/samar/HDD1T/Deep-EIoU/Deep-EIoU")
    return score


In [4]:
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=100)

[I 2024-06-05 00:03:27,041] A new study created in memory with name: no-name-df364314-93e5-4679-9baf-87922316bb0c
/media/samar/HDD1T/Deep-EIoU/Deep-EIoU/tools/torchreid/metrics/rank.py:11: UserWarning: Cython evaluation (very fast so highly recommended) is unavailable, now use python evaluation.
  warnings.warn(
2024-06-05 00:03:28.894160: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-06-05 00:03:28.923999: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-06-05 00:03:29.395614: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


yolox/yolox_x_ch_sportsmot.py None


2024-06-05 00:03:29.943 | INFO     | __main__:main:270 - Args: Namespace(experiment_name='yolox_x_ch_sportsmot', name=None, path='/media/samar/HDD1T/Deep-EIoU/Deep-EIoU/tools/test_videos/SNMOT-116.avi', save_result=True, exp_file='yolox/yolox_x_ch_sportsmot.py', ckpt=None, device=device(type='cuda'), conf=None, nms=None, tsize=None, fps=30, fp16=False, fuse=False, trt=False, track_high_thresh=0.9000000000000001, track_low_thresh=0.3, new_track_thresh=0.95, track_buffer=196, match_thresh=0.9000000000000001, aspect_ratio_thresh=1.6, min_box_area=10, nms_thres=0.05, mot20=False, with_reid=True, proximity_thresh=0.5, appearance_thresh=0.45)
/home/samar/anaconda3/envs/grad/lib/python3.11/site-packages/torch/functional.py:507: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at ../aten/src/ATen/native/TensorShape.cpp:3549.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]
2024-06-05 00:03:31.11

Successfully loaded pretrained weights from "checkpoints/sports_model.pth.tar-60"
** The following layers are discarded due to unmatched keys or layer size: ['classifier.weight', 'classifier.bias']


2024-06-05 00:03:38.441 | INFO     | __main__:imageflow_demo:202 - Processing frame 30 (5.97 fps)
2024-06-05 00:03:45.333 | INFO     | __main__:imageflow_demo:202 - Processing frame 60 (6.31 fps)
2024-06-05 00:03:52.456 | INFO     | __main__:imageflow_demo:202 - Processing frame 90 (6.37 fps)
2024-06-05 00:03:58.950 | INFO     | __main__:imageflow_demo:202 - Processing frame 120 (6.47 fps)
2024-06-05 00:04:05.302 | INFO     | __main__:imageflow_demo:202 - Processing frame 150 (6.56 fps)
2024-06-05 00:04:11.597 | INFO     | __main__:imageflow_demo:202 - Processing frame 180 (6.62 fps)
2024-06-05 00:04:17.796 | INFO     | __main__:imageflow_demo:202 - Processing frame 210 (6.68 fps)
2024-06-05 00:04:24.031 | INFO     | __main__:imageflow_demo:202 - Processing frame 240 (6.72 fps)
2024-06-05 00:04:30.269 | INFO     | __main__:imageflow_demo:202 - Processing frame 270 (6.76 fps)
2024-06-05 00:04:36.476 | INFO     | __main__:imageflow_demo:202 - Processing frame 300 (6.78 fps)
2024-06-05 00

...

[I 2024-06-06 17:22:38,623] Trial 17 finished with value: 0.6324674656000703 and parameters: {'track_high_thresh': 0.6000000000000001, 'track_low_thresh': 0.25, 'new_track_thresh': 0.45, 'track_buffer': 277, 'match_thresh': 0.2, 'nms_thres': 0.1, 'proximity_thresh': 0.7500000000000001, 'appearance_thresh': 0.2}. Best is trial 4 with value: 0.636984205993235.
/media/samar/HDD1T/Deep-EIoU/Deep-EIoU/tools/torchreid/metrics/rank.py:11: UserWarning: Cython evaluation (very fast so highly recommended) is unavailable, now use python evaluation.
  warnings.warn(
2024-06-06 17:22:40.488455: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-06-06 17:22:40.517212: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compile

yolox/yolox_x_ch_sportsmot.py None


2024-06-06 17:22:41.563 | INFO     | __main__:main:270 - Args: Namespace(experiment_name='yolox_x_ch_sportsmot', name=None, path='/media/samar/HDD1T/Deep-EIoU/Deep-EIoU/tools/test_videos/SNMOT-116.avi', save_result=True, exp_file='yolox/yolox_x_ch_sportsmot.py', ckpt=None, device=device(type='cuda'), conf=None, nms=None, tsize=None, fps=30, fp16=False, fuse=False, trt=False, track_high_thresh=0.4, track_low_thresh=0.05, new_track_thresh=0.55, track_buffer=506, match_thresh=0.15000000000000002, aspect_ratio_thresh=1.6, min_box_area=10, nms_thres=0.35000000000000003, mot20=False, with_reid=True, proximity_thresh=0.4, appearance_thresh=0.35000000000000003)
/home/samar/anaconda3/envs/grad/lib/python3.11/site-packages/torch/functional.py:507: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at ../aten/src/ATen/native/TensorShape.cpp:3549.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]
2024-

Successfully loaded pretrained weights from "checkpoints/sports_model.pth.tar-60"
** The following layers are discarded due to unmatched keys or layer size: ['classifier.weight', 'classifier.bias']


2024-06-06 17:22:45.059 | INFO     | __main__:imageflow_demo:192 - video save_path is ./YOLOX_outputs/yolox_x_ch_sportsmot/track_vis/2024_06_06_17_22_44/SNMOT-116.avi
2024-06-06 17:22:52.284 | INFO     | __main__:imageflow_demo:202 - Processing frame 30 (5.85 fps)
2024-06-06 17:22:59.588 | INFO     | __main__:imageflow_demo:202 - Processing frame 60 (6.10 fps)
2024-06-06 17:23:07.184 | INFO     | __main__:imageflow_demo:202 - Processing frame 90 (6.08 fps)
2024-06-06 17:23:14.552 | INFO     | __main__:imageflow_demo:202 - Processing frame 120 (6.11 fps)
2024-06-06 17:23:21.893 | INFO     | __main__:imageflow_demo:202 - Processing frame 150 (6.13 fps)


In [1]:
print("Best hyperparameters:", study.best_params)
print("Best value:", study.best_value)

NameError: name 'study' is not defined

In [ ]:
vis.plot_optimization_history(study)
vis.plot_param_importances(study)
vis.plot_slice(study)